In [1]:
import pyspedas
import pytplot
import numpy as np
import pandas as pd  # for csv data
import h5py
import datetime as dt
import os
import sys
from scipy.constants import physical_constants
os.environ["MMS_DATA_DIR"] = "/tigress/kendrab/analysis-notebooks/mms_data/pydata/"

### Parameters and unit conversion definitons

In [2]:
base_dir = '/tigress/kendrab/analysis-notebooks/mms_data/smith_dataset/'
rope_file = base_dir + 'A2.csv'
loop_file = base_dir + 'B2.csv'
rope_outfile = base_dir + 'rope_slices.h5'
loop_outfile = base_dir + 'loop_slices.h5'
negatives_outfile = base_dir + 'negative_slices.h5'

In [3]:
# Parameters (will change depending on which model we are using)
window = 89
stride = 11 
padding = (window-stride)/2
n_avg_width = 10  # for smoothing the plasma freq

# Physical constants (for unit conversion and plasma freq calc.)
c = physical_constants["speed of light in vacuum"][0]  # m/s
e = physical_constants["elementary charge"][0]  # coulombs
m_e = physical_constants["electron mass"][0]  # kg
m_i = physical_constants["proton mass"][0]  # kg
e_0 = physical_constants["vacuum electric permittivity"][0]  # Farads/m
k = physical_constants["Boltzmann constant"][0]  # J/K

# PIC characteristic values (MAKE SURE THESE ARE CORRECT FOR THE SIMULATION YOU ARE PROCESSING)
mime_pic = 25
v_the_sim_cs = 0.25
v_the_sim_out = 0.15
n_sim = 1
n_sim_out = 0.01/2.  # beta/2

# MMS characteristic values
b_burst_dt = dt.timedelta(seconds=1/128)
# assumed tail current sheet density, cm^-3
n_cs = 0.625
# assumed tail electron temperature, keV
e_the_tail = 3.795
# assumed lobe density, cm^-3 (Frank 1985)
n_lobe = 0.1
# assumed lobe temperature, K then J
e_the_lobe_K = 1e6
e_the_lobe_j = e_the_lobe_K*k

In [4]:
# Unit conversion and normalization supportive calculations
e_the_j = e_the_tail*1e3*e  # joules
print(e_the_j, e_the_lobe_j)
v_the_tail = np.sqrt(2*e_the_j/m_e)/c  # velocity in PIC units
v_the_lobe = np.sqrt(2*e_the_lobe_j/m_e)/c
print(v_the_tail, v_the_lobe)
print(v_the_sim_cs/v_the_tail, v_the_sim_out/v_the_lobe)
n_cs_m3 = n_cs*(100)**3  # cm^-3 to m^-3
plasma_freq = np.sqrt(n_cs_m3*e**2/e_0/m_e) #s^-1

# convert mms density to pic units
d_e = c/plasma_freq  # in m
n_cs_sim = n_cs_m3*d_e**3  # in d_e^(-3)
print('{:.2e}'.format(n_cs_sim))

6.08026032603e-16 1.3806490000000001e-17
0.12187394915783151 0.018365021386649957
2.0512997381929443 8.16770080698295
1.90e+17


In [5]:
# electric field correction...
# the units need to agree outside the log but inside the logs they just need to be locally consistent, because we are doing a ratio and the units are just a scale factor different
E_val_sim = np.sqrt(1/mime_pic)*v_the_sim_cs**2*np.log(n_sim_out*v_the_sim_out**2/(n_sim*v_the_sim_cs**2))
E_val_tail = np.sqrt(m_e/m_i)*(v_the_tail)**2*np.log(n_lobe*e_the_lobe_j/(n_cs*e_the_j))
E_corr_factor = E_val_sim/E_val_tail
print(E_val_sim, E_val_tail, E_corr_factor)

-0.07899960767600023 -0.0019472551195471386 40.56972652580453


In [6]:
# current density correction
j_val_sim = mime_pic**(-0.5)*n_sim*v_the_sim_cs**2
j_val_tail = np.sqrt(m_e/m_i)*n_cs_sim*v_the_tail**2
j_corr_factor = j_val_sim/j_val_tail
print(j_corr_factor)

1.8997442222394003e-16


In [7]:
# use A2.csv and B2.csv to get more stringently identified plasmoids (flux ropes and magnetic loops respectively) x
# convert times from format '%Y-%m-%d %H:%M:%S.XXX' to '%Y-%m-%d/%H:%M:%S' (maybe use datetime intermediary) x
# loop over intervals: (small modifications from mms_processing)  how to do pandas? x
#    Q: if no burst data, srvy or skip?
#    don't save intervals to different files, do the full processing into slices for each interval then slap them together to save outside the loop x
#    find a corresponding null sample for each interval (how? avoid all other plasmoids?? brainstorm)
# save in 4 files: rope_slices, loop_slices, rope_null_slices, loop_null_slices

### Helper functions

In [8]:
def ms_to_us(dt_string_ms):
    '''Adds 0 padding to the end of a time string ending with .ms so it is compatible with the %f format code in datetimes.
    e.g. HH:MM:SS.XXX -> HH:MM:SS.XXX000'''
    dt_string_us = dt_string_ms + '000'
    
    return dt_string_us

In [9]:
def time_str_conversions(df, series_name, offset = dt.timedelta(0)):
    ''' convert from smith string convention to datetime and pyspedas conventions
    putting each into new series in dataframe '''
    
    df[series_name+'_dt'] = df[series_name].map(lambda x: dt.datetime.strptime(ms_to_us(x), '%Y-%m-%d %H:%M:%S.%f')) + offset
    df[series_name+'_spedas'] = df[series_name+'_dt'].map(lambda x: x.strftime('%Y-%m-%d/%H:%M:%S.%f')[:-3])
    
    # no return bc df modified in-place(?)

In [10]:
def intervals_overlap(trange1, trange2):
    ''' returns True if the intervals interlap.
    trange1 = [start1, end1] '''
    overlap_start = max(trange1[0], trange2[0])
    overlap_end = min(trange1[1], trange2[1])
    overlap = overlap_end - overlap_start
    
    return overlap > dt.timedelta(0)

### Main loop function

In [11]:
def processing_loop(df, outfile):
    ''' Main loop for taking dataframe with segment data and turning it into model-ready slices. '''
    sliced_B_list=[]
    sliced_E_list=[]
    sliced_j_list=[]
    sliced_time_list=[]
    sliced_structure_list = []
    
    for row in df.itertuples():
        print(f"Starting row index {row.Index}")
        trange = [row.Start_spedas, row.End_spedas]
        #### FPI data
        vars_tmp = pyspedas.mms.fpi(trange=trange, probe='1', data_rate='brst', datatype='des-moms',
                                    time_clip=True, varnames=["mms1_des_numberdensity_brst"])
        if vars_tmp is None: 
            print(f"Missing FPI data for interval {trange}")
            pytplot.del_data()
            continue
        #### MEC data 
        mec_datarate = 'brst'  # pull this into its own variable in case we want to record whether we used brst or srvy
        vars_tmp = np.empty(4, dtype=object)
        for j in range(1,5):
            vars_tmp[j-1] = pyspedas.mms.mec(trange=trange, probe=str(j), data_rate=mec_datarate, time_clip=False,
                                        varnames=[f"mms{j}_mec_r_gse",])
        if np.any(vars_tmp == None):  # no burst data
            print(f"Missing some MEC burst data, interval {trange}. Trying survey data")
            mec_datarate = 'srvy'
            vars_tmp = np.empty(4, dtype=object)   
            for j in range(1,5):  # try srvy data
                try:
                    vars_tmp[j-1] = pyspedas.mms.mec(trange=trange, probe=str(j), data_rate=mec_datarate, time_clip=False,
                                                     varnames=[f"mms{j}_mec_r_gse",])
                except:
                    vars_tmp = np.empty(4, dtype=object)
            if np.any(vars_tmp == None):  # no srvy data 
                print(f"Missing some MEC data, interval {trange}")
                pytplot.del_data()
                continue
        #### FGM data    
        vars_tmp = np.empty(4, dtype=object)
        for j in range(1,5):
            vars_tmp[j-1] = pyspedas.mms.fgm(trange=trange, probe=str(j), data_rate='brst', time_clip=True,
                                        varnames=[f"mms{j}_fgm_b_gsm_brst_l2",])
        if np.any(vars_tmp == None):
            print(f"Missing some FGM data, interval {trange}")
            pytplot.del_data()
            continue
        #### EDP data
        vars_tmp = pyspedas.mms.edp(trange=trange, probe='1', data_rate='brst', time_clip=True,
                                    varnames=["mms1_edp_dce_gse_brst_l2"]) 
        if vars_tmp is None:
            print(f"Missing EDP data for interval {trange}")
            pytplot.del_data()
            continue
            
        # # optional info printouts    
        # print(pytplot.data_quants.keys())
        # print(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2"].shape, pytplot.data_quants["mms1_edp_dce_gse_brst_l2"].shape)
        # print(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2"])
        # print(pytplot.data_quants["mms1_edp_dce_gse_brst_l2"])
        
        # remove duplicates from data 
        pytplot.data_quants["mms1_edp_dce_gse_brst_l2"] = pytplot.data_quants["mms1_edp_dce_gse_brst_l2"].drop_duplicates(dim='time', keep='first')
        for j in range(1,5):
            pytplot.data_quants[f"mms{j}_fgm_b_gsm_brst_l2_bvec"] = pytplot.data_quants[f"mms{j}_fgm_b_gsm_brst_l2_bvec"].drop_duplicates(dim='time', keep='first')
            pytplot.data_quants[f"mms{j}_mec_r_gse"] = pytplot.data_quants[f"mms{j}_mec_r_gse"].drop_duplicates(dim='time', keep='first')
            
        # Find curlometer j- need to move to GSE and interpolate r for this
        fields=[]
        pos = []
        for j in range(1,5):
            pyspedas.cotrans(name_in = f"mms{j}_fgm_b_gsm_brst_l2_bvec", name_out = f"mms{j}_fgm_b_gse_brst_l2_bvec",
                             coord_in='gsm', coord_out='gse')
            fields.append(f"mms{j}_fgm_b_gse_brst_l2_bvec")
            pos.append(f"mms{j}_mec_r_gse")
        pyspedas.mms.curlometer(fields=fields, positions=pos) # jtotal in A/m^2
        # print(pytplot.data_quants['jtotal'])  # optional info printout
        
        # Interpolate E (and possibly B if we want to) to a lower data rate
        pytplot.data_quants["mms1_edp_dce_gse_brst_l2"] = \
            pytplot.data_quants["mms1_edp_dce_gse_brst_l2"].interp(method="linear", assume_sorted=False,
                                                                   time=pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)
        # use pyspedas to transform E field and j data to GSM coordinates
        pyspedas.cotrans(name_in="mms1_edp_dce_gse_brst_l2", name_out="mms1_edp_dce_gsm_brst_l2", coord_in='gse', coord_out='gsm')
        pyspedas.cotrans(name_in="jtotal", name_out="jtotal_gsm", coord_in='gse', coord_out='gsm')
        
        # Convert E, B, J to typical PIC units e = 1, m_e = 1, c = 1, d_e = 1, w_pe = 1
        pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"] *= 10**(-9)/m_e*e/plasma_freq  # T/nT*m_e/kg*C/e*(wpe^-1*s) -> units of m_e wpe / e #TODO FIX THESE
        pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"] *= 10**(-3)/m_e*e/plasma_freq/c  # V/mV*m_e/kg*C/e*(wpe^-1*s)*(c / m/s) -> units of m_e wpe c / e 
        pytplot.data_quants["jtotal_gsm"] *= c*c/plasma_freq**3/e  # units of e wpe^3/c^2 or e wpe / de^2
        
        # Scale E and j based on parameter differences between PIC and MMS data
        pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"] *= E_corr_factor
        pytplot.data_quants["jtotal_gsm"] *= j_corr_factor
        
        # group the data to get rid of data gaps
        next_time_interval = np.diff(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)
        timestep_max = 1.1*np.median(next_time_interval) # bigger than a timestep to avoid float inaccuracy nonsense
        pre_gap_idxs = np.nonzero(next_time_interval > timestep_max)
        bin_idxs = [0,] + list(pre_gap_idxs[0]) + [len(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)-1,]  # using real idx instead of -1 to avoid sorting issues
        bin_idxs = np.unique(bin_idxs)
        groups_B_cots = pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].groupby_bins("time", bins=pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time[bin_idxs].sortby("time"),
                                                                                  include_lowest=True)
        groups_E_cots = pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"].groupby_bins("time", bins=pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"].time[bin_idxs].sortby("time"),
                                                                                  include_lowest=True)
        groups_j_cots = pytplot.data_quants["jtotal_gsm"].groupby_bins("time", bins=pytplot.data_quants["jtotal"].time[bin_idxs].sortby("time"), include_lowest=True)
        
        for B_arr, E_arr, j_arr in zip(groups_B_cots, groups_E_cots, groups_j_cots): 
            if len(B_arr[1].time) > window:
                B_slices = np.lib.stride_tricks.sliding_window_view(B_arr[1].values, window, axis=0)[::stride,:,:].copy()
                E_slices = np.lib.stride_tricks.sliding_window_view(E_arr[1].values, window, axis=0)[::stride,:].copy()
                j_slices = np.lib.stride_tricks.sliding_window_view(j_arr[1].values, window, axis=0)[::stride,:].copy()                                                                                                    
                time_slices = np.lib.stride_tricks.sliding_window_view(B_arr[1].time.values, window, axis=0)[::stride,:].copy()

                sliced_B_list.append(B_slices)
                sliced_E_list.append(E_slices)
                sliced_j_list.append(j_slices)
                sliced_time_list.append(time_slices)
                sliced_structure_list.append(np.full_like(time_slices, row.Index, dtype=int))  # yay this one has enough data for us to be happy
            else:
                print(f"Segment too short for sliding window view with length {len(B_arr[1].time)}")  
        # unload this slice's unneeded tplot data
        pytplot.del_data()
                
    # save sliced data
    sliced_B = np.concatenate(sliced_B_list, axis=0)
    sliced_E = np.concatenate(sliced_E_list, axis=0)
    sliced_j = np.concatenate(sliced_j_list, axis=0)
    sliced_time = np.concatenate(sliced_time_list, axis=0, dtype='datetime64[us]')
    sliced_time = sliced_time.astype(object)
    sliced_time = np.vectorize(lambda x: x.strftime('%Y-%m-%dT%H:%M:%S.%f').encode('ascii'))(sliced_time)
    sliced_struct_num = np.concatenate(sliced_structure_list, axis=0)
    # remove data that has nans in it
    # check j and E then filter all
    clean_j_idxs = ~np.isnan(sliced_j).any(axis=(1,2))
    clean_E_idxs = ~np.isnan(sliced_E).any(axis=(1,2))
    clean_idxs = np.logical_and(clean_j_idxs, clean_E_idxs)
    print(f"Samples: {sliced_j.shape[0]}  Samples with no NaNs: {np.sum(clean_idxs)}")

    with h5py.File(outfile,'w') as file:
        file.create_dataset('B', data=sliced_B[clean_idxs])
        file.create_dataset('E', data=sliced_E[clean_idxs])
        file.create_dataset('j', data=sliced_j[clean_idxs])
        file.create_dataset('time', data=sliced_time[clean_idxs])
        file.create_dataset('struct_num', data=sliced_struct_num[clean_idxs])

### Negatives loop function

In [12]:
# how to find negative/no-plasmoid slices: want same time size as each interval, similar plasma condition
# try interval directly before the plasmoid (w/ a little space)
# IF it overlaps with any other interval (loops, ropes, or existing nulls) RETRY in order:
#    interval directly after the plasmoid
#    interval before interval before plasmoid
#    interval after interval after plasmoid
# repeat at infinitum until we find a non-overlapping interval (that has burst data?)
# this is going to be slow AF unless I think of a better way :/
def find_negatives_loop(dfs, outfile, spacing=dt.timedelta(minutes=0.5), max_tries=10):
    """ Finding non-plasmoid slices to balance our dataset """
    neg_intervals=[]
    sliced_B_list=[]
    sliced_E_list=[]
    sliced_j_list=[]
    sliced_time_list=[]
    
    for df in dfs:
        for row in df.itertuples():
            try_num = 1
            trange = [row.Start_dt, row.End_dt]
            interval_len = trange[1] - trange[0]
            # hoo boy here we go
            while try_num > 0:
                offset = spacing + try_num*interval_len
                interval_before = [trange[0] - offset, trange[1] - offset]
                interval_after = [trange[0] + offset, trange[1] + offset]
                collision_before = False
                collision_after = False
                # check our candidate intervals against EVERY other interval ://///
                for neg_interval in neg_intervals:
                    collision_before = collision_before or intervals_overlap(neg_interval, interval_before)
                    collision_after = collision_after or intervals_overlap(neg_interval, interval_after)
                    if collision_before and collision_after:  # these candidates are dead
                        break  # break out of neg_intervals for loop
                if collision_before and collision_after:
                    print(f"Try number {try_num} failed due to interval overlap")
                    if try_num >= max_tries:
                        print(f"Reached maximum number of tries {try_num}, skipping interval.")
                        break  
                    else:
                        try_num += 1
                        continue
                for df2 in dfs:  # check against all dataframes now
                    for row2 in df2.itertuples():
                        trange2 = [row2.Start_dt, row2.End_dt]
                        collision_before = collision_before or intervals_overlap(trange2, interval_before)
                        collision_after = collision_after or intervals_overlap(trange2, interval_after)
                        if collision_before and collision_after:  # these candidates are dead
                            break  # break out of inner for loop
                    if collision_before and collision_after:
                        break  # break out of outer for loop 
                if collision_before and collision_after:
                    print(f"Try number {try_num} failed due to interval overlap")
                    if try_num >= max_tries:
                        print(f"Reached maximum number of tries {try_num}, skipping interval.")
                        break  
                    else:
                        try_num += 1
                        continue
                # if we made it here, either before or after had no collisions, yippee! now check for burst data availability ://///////
                ok_intervals = []
                if not collision_before:
                    ok_intervals.append(interval_before)
                if not collision_after:
                    ok_intervals.append(interval_after)
                # try all possible candidate intervals
                print(f"Trying candidate negative intervals {ok_intervals} from plasmoid interval {trange}")
                interval_succeeded = False
                for ok_interval in ok_intervals:
                    if interval_succeeded:  # don't need to run again for the second ok interval
                        break
                    ok_interval_str = [ok_interval[0].strftime('%Y-%m-%d/%H:%M:%S.%f')[:-3],ok_interval[1].strftime('%Y-%m-%d/%H:%M:%S.%f')[:-3]]
                     #### FPI data
                    vars_tmp = pyspedas.mms.fpi(trange=ok_interval_str, probe='1', data_rate='brst', datatype='des-moms',
                                                time_clip=True, varnames=["mms1_des_numberdensity_brst"])
                    if vars_tmp is None: 
                        print(f"Missing FPI data for interval {ok_interval_str}")
                        pytplot.del_data()
                        continue                        
                    #### MEC data 
                    mec_datarate = 'brst'  # pull this into its own variable in case we want to record whether we used brst or srvy
                    vars_tmp = np.empty(4, dtype=object)
                    for j in range(1,5):
                        vars_tmp[j-1] = pyspedas.mms.mec(trange=ok_interval_str, probe=str(j), data_rate=mec_datarate, time_clip=False,
                                                    varnames=[f"mms{j}_mec_r_gse",])
                    if np.any(vars_tmp == None):  # no burst data
                        print(f"Missing some MEC burst data, interval {ok_interval}. Trying survey data")
                        mec_datarate = 'srvy'
                        vars_tmp = np.empty(4, dtype=object)   
                        for j in range(1,5):  # try srvy data
                            try:
                                vars_tmp[j-1] = pyspedas.mms.mec(trange=ok_interval_str, probe=str(j), data_rate=mec_datarate, time_clip=False,
                                                                 varnames=[f"mms{j}_mec_r_gse",])
                            except:
                                vars_tmp = np.empty(4, dtype=object)
                        if np.any(vars_tmp == None):  # no srvy data 
                            print(f"Missing some MEC data, interval {ok_interval}")
                            pytplot.del_data()
                            continue
                    #### FGM data    
                    vars_tmp = np.empty(4, dtype=object)
                    for j in range(1,5):
                        vars_tmp[j-1] = pyspedas.mms.fgm(trange=ok_interval_str, probe=str(j), data_rate='brst', time_clip=True,
                                                    varnames=[f"mms{j}_fgm_b_gsm_brst_l2",])
                    if np.any(vars_tmp == None):
                        print(f"Missing some FGM data, interval {ok_interval}")
                        pytplot.del_data()
                        continue
                    #### EDP data
                    vars_tmp = pyspedas.mms.edp(trange=ok_interval_str, probe='1', data_rate='brst', time_clip=True,
                                                varnames=["mms1_edp_dce_gse_brst_l2"]) 
                    if vars_tmp is None:
                        print(f"Missing EDP data for interval {ok_interval}")
                        pytplot.del_data()
                        continue
                     # remove duplicates from data 
                    pytplot.data_quants["mms1_edp_dce_gse_brst_l2"] = pytplot.data_quants["mms1_edp_dce_gse_brst_l2"].drop_duplicates(dim='time', keep='first')
                    for j in range(1,5):
                        pytplot.data_quants[f"mms{j}_fgm_b_gsm_brst_l2_bvec"] = pytplot.data_quants[f"mms{j}_fgm_b_gsm_brst_l2_bvec"].drop_duplicates(dim='time', keep='first')
                        pytplot.data_quants[f"mms{j}_mec_r_gse"] = pytplot.data_quants[f"mms{j}_mec_r_gse"].drop_duplicates(dim='time', keep='first')

                    # Find curlometer j- need to move to GSE and interpolate r for this
                    fields=[]
                    pos = []
                    for j in range(1,5):
                        pyspedas.cotrans(name_in = f"mms{j}_fgm_b_gsm_brst_l2_bvec", name_out = f"mms{j}_fgm_b_gse_brst_l2_bvec",
                                         coord_in='gsm', coord_out='gse')
                        fields.append(f"mms{j}_fgm_b_gse_brst_l2_bvec")
                        pos.append(f"mms{j}_mec_r_gse")
                    pyspedas.mms.curlometer(fields=fields, positions=pos) # jtotal in A/m^2
                    # print(pytplot.data_quants['jtotal'])  # optional info printout

                    # Interpolate E (and possibly B if we want to) to a lower data rate
                    pytplot.data_quants["mms1_edp_dce_gse_brst_l2"] = \
                        pytplot.data_quants["mms1_edp_dce_gse_brst_l2"].interp(method="linear", assume_sorted=False,
                                                                               time=pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)
                    # use pyspedas to transform E field and j data to GSM coordinates
                    pyspedas.cotrans(name_in="mms1_edp_dce_gse_brst_l2", name_out="mms1_edp_dce_gsm_brst_l2", coord_in='gse', coord_out='gsm')
                    pyspedas.cotrans(name_in="jtotal", name_out="jtotal_gsm", coord_in='gse', coord_out='gsm')

                    # Convert E, B, J to typical PIC units e = 1, m_e = 1, c = 1, d_e = 1, w_pe = 1
                    pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"] *= 10**(-9)/m_e*e/plasma_freq  # T/nT*m_e/kg*C/e*(wpe^-1*s) -> units of m_e wpe / e #TODO FIX THESE
                    pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"] *= 10**(-3)/m_e*e/plasma_freq/c  # V/mV*m_e/kg*C/e*(wpe^-1*s)*(c / m/s) -> units of m_e wpe c / e 
                    pytplot.data_quants["jtotal_gsm"] *= c*c/plasma_freq**3/e  # units of e wpe^3/c^2 or e wpe / de^2

                    # Scale E and j based on parameter differences between PIC and MMS data
                    pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"] *= E_corr_factor
                    pytplot.data_quants["jtotal_gsm"] *= j_corr_factor

                    # group the data to get rid of data gaps
                    next_time_interval = np.diff(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)
                    timestep_max = 1.1*np.median(next_time_interval) # bigger than a timestep to avoid float inaccuracy nonsense
                    pre_gap_idxs = np.nonzero(next_time_interval > timestep_max)
                    bin_idxs = [0,] + list(pre_gap_idxs[0]) + [len(pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time)-1,]  # using real idx instead of -1 to avoid sorting issues
                    bin_idxs = np.unique(bin_idxs)
                    groups_B_cots = pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].groupby_bins("time", bins=pytplot.data_quants["mms1_fgm_b_gsm_brst_l2_bvec"].time[bin_idxs].sortby("time"),
                                                                                              include_lowest=True)
                    groups_E_cots = pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"].groupby_bins("time", bins=pytplot.data_quants["mms1_edp_dce_gsm_brst_l2"].time[bin_idxs].sortby("time"),
                                                                                              include_lowest=True)
                    groups_j_cots = pytplot.data_quants["jtotal_gsm"].groupby_bins("time", bins=pytplot.data_quants["jtotal"].time[bin_idxs].sortby("time"), include_lowest=True)

                    for B_arr, E_arr, j_arr in zip(groups_B_cots, groups_E_cots, groups_j_cots): 
                        if len(B_arr[1].time) > window:
                            B_slices = np.lib.stride_tricks.sliding_window_view(B_arr[1].values, window, axis=0)[::stride,:,:].copy()
                            E_slices = np.lib.stride_tricks.sliding_window_view(E_arr[1].values, window, axis=0)[::stride,:].copy()
                            j_slices = np.lib.stride_tricks.sliding_window_view(j_arr[1].values, window, axis=0)[::stride,:].copy()                                                                                                    
                            time_slices = np.lib.stride_tricks.sliding_window_view(B_arr[1].time.values, window, axis=0)[::stride,:].copy()

                            sliced_B_list.append(B_slices)
                            sliced_E_list.append(E_slices)
                            sliced_j_list.append(j_slices)
                            sliced_time_list.append(time_slices)
                        else:
                            print(f"Segment too short for sliding window view with length {len(B_arr[1].time)}")  
                    # unload this slice's unneeded tplot data
                    pytplot.del_data() 
                    # we were successful, yay
                    neg_intervals.append(ok_interval)
                    interval_succeeded = True
                # either continue (if all intervals failed) or end loop
                if not interval_succeeded:
                    print(f"Try number {try_num} failed due to lack of data")
                    if try_num >= max_tries:
                        print(f"Reached maximum number of tries {try_num}, skipping interval.")
                        break                    
                    else:
                        try_num +=1
                        continue
                else: # we are FREEEEEEE for this interval
                    print(f"Try number {try_num} succeeded")
                    try_num = -1
                    continue
    # save sliced data
    sliced_B = np.concatenate(sliced_B_list, axis=0)
    sliced_E = np.concatenate(sliced_E_list, axis=0)
    sliced_j = np.concatenate(sliced_j_list, axis=0)
    sliced_time = np.concatenate(sliced_time_list, axis=0, dtype='datetime64[us]')
    sliced_time = sliced_time.astype(object)
    sliced_time = np.vectorize(lambda x: x.strftime('%Y-%m-%dT%H:%M:%S.%f').encode('ascii'))(sliced_time)
    # remove data that has nans in it
    # check j and E then filter all
    clean_j_idxs = ~np.isnan(sliced_j).any(axis=(1,2))
    clean_E_idxs = ~np.isnan(sliced_E).any(axis=(1,2))
    clean_idxs = np.logical_and(clean_j_idxs, clean_E_idxs)
    print(f"Samples: {sliced_j.shape[0]}  Samples with no NaNs: {np.sum(clean_idxs)}")

    with h5py.File(outfile,'w') as file:
        file.create_dataset('B', data=sliced_B[clean_idxs])
        file.create_dataset('E', data=sliced_E[clean_idxs])
        file.create_dataset('j', data=sliced_j[clean_idxs])
        file.create_dataset('time', data=sliced_time[clean_idxs])
    

### Main code

In [13]:
rope_df = pd.read_csv(rope_file)
loop_df = pd.read_csv(loop_file)
# pad the time intervals with the amount of padding used in the model
# thus ensuring plasmoids at least <stride> points long can be used
# but without having non-plasmoid data in the center prediction bit of any slice
padding_time = padding*b_burst_dt
print(padding_time)
print(rope_df["Start"])
# get datetime and convert to pyspedas-friendly string format
time_str_conversions(rope_df, 'Start', offset=-padding_time)
print(rope_df["Start_spedas"])
time_str_conversions(rope_df, 'End', offset=padding_time)
time_str_conversions(loop_df, 'Start', offset=-padding_time)
time_str_conversions(loop_df, 'End', offset=padding_time)


0:00:00.304668
0      2017-06-28 08:21:07.750
1      2017-06-28 15:24:52.250
2      2017-06-28 16:19:18.750
3      2017-06-28 16:20:13.250
4      2017-06-28 16:32:21.250
                ...           
176    2022-07-12 02:08:16.250
177    2022-07-12 06:16:57.250
178    2022-07-12 06:20:38.750
179    2022-07-19 06:12:30.750
180    2022-07-21 23:53:43.750
Name: Start, Length: 181, dtype: object
0      2017-06-28/08:21:07.445
1      2017-06-28/15:24:51.945
2      2017-06-28/16:19:18.445
3      2017-06-28/16:20:12.945
4      2017-06-28/16:32:20.945
                ...           
176    2022-07-12/02:08:15.945
177    2022-07-12/06:16:56.945
178    2022-07-12/06:20:38.445
179    2022-07-19/06:12:30.445
180    2022-07-21/23:53:43.445
Name: Start_spedas, Length: 181, dtype: object


In [14]:
# # process each segment
# processing_loop(rope_df, rope_outfile)
# processing_loop(loop_df, loop_outfile)

In [15]:
# find outside values
find_negatives_loop([rope_df, loop_df], negatives_outfile)

Trying candidate negative intervals [[Timestamp('2017-06-28 08:20:28.835996'), Timestamp('2017-06-28 08:20:37.445332')], [Timestamp('2017-06-28 08:21:46.054668'), Timestamp('2017-06-28 08:21:54.664004')]] from plasmoid interval [Timestamp('2017-06-28 08:21:07.445332'), Timestamp('2017-06-28 08:21:16.054668')]
Loading /tigress/kendrab/analysis-notebooks/mms_data/pydata/mms1/fpi/brst/l2/des-moms/2017/06/28/mms1_fpi_brst_l2_des-moms_20170628081923_v3.3.0.cdf
Time clip was applied to: mms1_des_numberdensity_brst
The name mms1_des_errorflags_brst is currently not in pytplot
The name mms1_des_compressionloss_brst is currently not in pytplot
The name mms1_des_pitchangdist_lowen_brst is currently not in pytplot
The name mms1_des_pitchangdist_miden_brst is currently not in pytplot
The name mms1_des_pitchangdist_highen_brst is currently not in pytplot
The name mms1_des_errorflags_brst_moms is currently not in pytplot
The name mms1_des_errorflags_brst_moms is currently not in pytplot
The name mms

13-Nov-24 12:58:25: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")



tinterpol (linear) was applied to: mms2_fgm_b_gse_brst_l2_bvec_i


13-Nov-24 12:58:25: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")



tinterpol (linear) was applied to: mms3_fgm_b_gse_brst_l2_bvec_i


...

tinterpol (linear) was applied to: mms4_mec_r_gse_i


13-Nov-24 14:08:41: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")



['gse', 'gsm']
Running transformation: subgse2gsm
Output variable: mms1_edp_dce_gsm_brst_l2
['gse', 'gsm']
Running transformation: subgse2gsm
Output variable: jtotal_gsm


13-Nov-24 14:08:41: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")

13-Nov-24 14:08:41: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")

13-Nov-24 14:08:41: /home/kendrab/.conda/envs/pyspedas/lib/python3.7/site-packages/xarray/core/pycompat.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  duck_array_version = LooseVersion("0.0.0")



Try number 1 succeeded
Samples: 58342  Samples with no NaNs: 38093
